In [1]:
import sys
    
import numpy as np

import os

import plotly.graph_objects as go

try:
    import nPDyn
    from nPDyn.models.params import Parameters
    from nPDyn.models.model import Model, Component
except ModuleNotFoundError or ImportError:
    !{sys.executable} -m pip install git+https://github.com/kpounot/nPDyn@dev_lmfit#egg=nPDyn

    import nPDyn
    from nPDyn.models.params import Parameters
    from nPDyn.models.model import Model, Component

## Instanciating a model, here a weighed pseudo-Voigt profile

In [20]:
X = np.arange(-30, 30, 0.01)
q = np.arange(0.2, 2, 0.15)[:, np.newaxis]

def lorentzian(x, amplitude, sigma, center):
    return amplitude / np.pi * sigma / ((x - center)**2 + sigma**2)

def gaussian(x, amplitude, sigma, center):
    return amplitude / np.sqrt(2*np.pi*sigma**2) * np.exp(-x**2 / (2 * sigma**2))

p = Parameters(
    amplitude=(np.zeros_like(q) + 0.5, (0., np.inf)),
    sigma={'value': 0.3, 'bounds': (0., np.inf)},
    center={'value': 0., 'fixed': True})

m = Model(params=p)
m.eisfComponents['pvoigt_lor'] = Component(lorentzian, amplitude='np.exp(-1.2*q**2/6) * amplitude', 
                                                       sigma='sigma')
m.eisfComponents['pvoigt_gau'] = Component(gaussian, 
                                           amplitude='1 - np.exp(-1.2*q**2/6) * amplitude',
                                           sigma='sigma / np.sqrt(2 * np.log(2))')

## Plotting the model

In [23]:
fig = go.FigureWidget(layout=go.Layout(xaxis={'title': m.xLabel},
                                       yaxis={'title': m.yLabel, 'type':'log'}))

for idx, val in enumerate(m.getModel(X, q=q)):
    fig.add_trace(go.Scatter(x=X, y=val, name="q = %.2f" % q[idx]))

fig.show()
